In [3]:
import numpy as np
import pandas as pd

import tensorflow as tf
from tensorflow import gfile

from collections import Counter
from itertools import combinations

C:\ProgramData\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [4]:
## Lees csv-files in
csv_path = 'csv_files/'
mid_to_label_new = pd.read_csv(str(csv_path) + 'class_labels_indices_amsterdam.csv', quotechar = '"')
balanced_train_segments = pd.read_csv(str(csv_path) + 'balanced_train_segments.csv', sep = ";")
unbalanced_train_segments = pd.read_csv(str(csv_path) + 'unbalanced_train_segments.csv', sep = ";")

In [5]:
## Verkrijg alle labels en labelcombinaties (uit csv-file)
def getLabelOccurences(segments_file):
    
    ## Houd labels bij en label-combinaties (elke combi uit een example)
    labels = []
    label_combinations = []

    # for each row
    for i in range(segments_file.shape[0]):

        # labels uit de example
        label_combination = []
        mids = segments_file.loc[i, 'positive_labels'].split(",")
        
        # for each m-id in a string
        for mid in mids:
            new_label = mid_to_label_new.loc[mid_to_label_new['mid']==str(mid), 'index']
            
            if(new_label.shape[0]>0):
                labels.extend(new_label)
                new_label_combi = str(new_label.values[0])
                label_combination.extend(new_label_combi)
    
        if len(label_combination)>0:
            label_combinations.append(label_combination)
    
    return(labels, label_combinations)

In [7]:
## Kies of je de balanced of unbalanced set wilt lezen
bal_labels, bal_label_combinations = getLabelOccurences(balanced_train_segments)
#unbal_labels, unbal_label_combinations = getLabelOccurences(unbalanced_train_segments)

In [10]:
## Houd totale aantal bij
sum_occur = 0
all_labels = unbal_labels # bal_labels

## Laat # voorkomens per label zien
cnt_labels = Counter(all_labels)
for i in cnt_labels.most_common(len(all_labels)):
    sum_occur = sum_occur + i[1]
    print(mid_to_label_new.loc[np.int(i[0])]['display_name'], ' : ', str(i[1]))

Music  :  5146
Speech  :  2241
Vehicle  :  714
Musical instrument  :  497
Domestic animals, pets  :  410
Boat, Water vehicle  :  242
Rail transport  :  186
Gunshot, gunfire  :  177
Emergency vehicle  :  141
Animal  :  123
Car  :  121
Tools  :  93
Ambulance (siren)  :  69
Motor vehicle (road)  :  63
Motor vehicle (road)  :  63
Fire engine, fire truck (siren)  :  60
Motorcycle  :  58
Accelerating, revving, vroom  :  57
Idling  :  55
Bus  :  54
Conversation  :  47
Chainsaw  :  35
Vehicle horn, car horn, honking  :  35
Jackhammer  :  33
Aircraft  :  29
Traffic noise, roadway noise  :  23
Medium engine (mid frequency)  :  13
Hammer  :  10
Machine gun  :  9
Police car (siren)  :  4
Heavy engine (low frequency)  :  3
Power tool  :  2


In [13]:
label_combinations = unbal_label_combinations

## Bereken aantal voorkomens per combinatie
cnt_label_combinations = Counter(seq[i:j]
                   for seq in map(tuple, label_combinations)
                   for i, j in combinations(range(len(seq) + 1), 2))

In [14]:
## Haal labelnaam op en print aantal voorkomens (met top x)
for label_combination in cnt_label_combinations.most_common(1000):
    
    if(label_combination[1]<2): # vanaf 2x voorkomen
        break;
        
    label_names = []
    for i in label_combination[0]:
        label_names.append(str(mid_to_label_new.loc[np.int(i)]['display_name']))
    label_names = ', '.join(label_names)
    print(label_names,': ', label_combination[1])

Music :  5217
Speech :  2273
Animal :  786
Vehicle :  781
Musical instrument :  734
Conversation :  703
Domestic animals, pets :  619
Music, Musical instrument :  482
Music, Speech :  406
Boat, Water vehicle :  265
Rail transport :  234
Motor vehicle (road) :  219
Conversation, Musical instrument :  177
Vehicle, Speech :  168
Domestic animals, pets, Speech :  154
Animal, Animal :  145
Conversation, Motor vehicle (road) :  121
Vehicle, Conversation :  110
Domestic animals, pets, Animal :  102
Conversation, Conversation :  96
Animal, Vehicle :  81
Vehicle, Conversation, Motor vehicle (road) :  79
Musical instrument, Speech :  78
Music, Musical instrument, Speech :  77
Speech, Animal :  72
Animal, Music :  69
Music, Animal :  69
Animal, Music, Animal :  66
Animal, Musical instrument :  60
Animal, Musical instrument, Animal :  60
Animal, Musical instrument, Animal, Animal :  60
Musical instrument, Animal :  60
Musical instrument, Animal, Animal :  60
Domestic animals, pets, Domestic animal

In [153]:
## Code die kolom toevoegt aan label-csv (proportion) en deze in de forloop vult

mid_to_label_new["proportion"] = 0

for i in range(mid_to_label_new.shape[0]):
    nr_occur = cnt_labels[i]
    mid_to_label_new.loc[i,"proportion"] = round(nr_occur/sum_occur,8)

In [154]:
## Schrijf bestandje weg
mid_to_label_new.to_csv(str(csv_path) + "class_labels_indices_proportions.csv", sep = ";")

In [ ]:
###############################################################################
####
###############################################################################
#### Hieronder staat andere code (deze code telt de labels vanuit tf-records)

In [15]:
## Hieronder worden labels geteld door het lezen van tf-records
all_labels = []
label_combinations = []

In [17]:
## Folder met tf-records
train_data_pattern = 'tfrecords/train_data_new/*.tfrecord'
test_data_pattern = 'tfrecords/test_data_new/*.tfrecord'

In [108]:
def getLabelsFromTfRecord(tfrecords_filename):
    
    ## Iterator that goes through all examples of tf-record
    record_iterator = tf.python_io.tf_record_iterator(path=tfrecords_filename)
   
    label_combination = []
    
    for string_record in record_iterator:
        
        ## Take one example
        example = tf.train.SequenceExample()
        example.ParseFromString(string_record)
 
        ## Get labels
        new_labels = example.context.feature['labels'].int64_list.value
        print("new_labels: " + str(new_labels))
        for label in new_labels:
            all_labels.append(int(label))
        label_combination.extend(new_labels)

    label_combinations.append(label_combination)

In [109]:
## Labels uit tf-records
files = gfile.Glob(train_data_pattern)

for file in files:
    print("file: " + file)
   
    getLabelsFromTfRecord(file)

file: tfrecords\train_data_new\--.tfrecord
new_labels: [0, 4]
new_labels: [15]
file: tfrecords\train_data_new\-0.tfrecord
new_labels: [0, 4]
new_labels: [4, 5]
file: tfrecords\train_data_new\-2.tfrecord
new_labels: [29, 32]
file: tfrecords\train_data_new\-3.tfrecord
new_labels: [7]
new_labels: [0, 6]
file: tfrecords\train_data_new\-4.tfrecord
new_labels: [22, 24]
file: tfrecords\train_data_new\-5.tfrecord
new_labels: [0, 4, 5]
file: tfrecords\train_data_new\-6.tfrecord
new_labels: [0, 4]
new_labels: [0, 3]
file: tfrecords\train_data_new\-7.tfrecord
new_labels: [6, 31]
new_labels: [0, 4]
new_labels: [4, 6]
file: tfrecords\train_data_new\-8.tfrecord
new_labels: [0, 6]
file: tfrecords\train_data_new\-A.tfrecord
new_labels: [0, 6]
new_labels: [20]
new_labels: [0, 4]
file: tfrecords\train_data_new\-B.tfrecord
new_labels: [0, 4]
new_labels: [2, 3]
file: tfrecords\train_data_new\-c.tfrecord
new_labels: [15]
new_labels: [15]
new_labels: [0, 4]
file: tfrecords\train_data_new\-F.tfrecord
new_lab

file: tfrecords\train_data_new\Mk.tfrecord
new_labels: [0, 6, 18, 19]
file: tfrecords\train_data_new\ML.tfrecord
new_labels: [4, 5]
new_labels: [2, 3]
new_labels: [12]
file: tfrecords\train_data_new\mM.tfrecord
new_labels: [4, 5]
file: tfrecords\train_data_new\mn.tfrecord
new_labels: [0, 4, 6, 21]
file: tfrecords\train_data_new\mO.tfrecord
new_labels: [0, 4]
new_labels: [0, 4]
new_labels: [0, 4]
new_labels: [30]
file: tfrecords\train_data_new\Mq.tfrecord
new_labels: [4]
file: tfrecords\train_data_new\mR.tfrecord
new_labels: [4, 5]
new_labels: [0, 4]
file: tfrecords\train_data_new\mt.tfrecord
new_labels: [6, 18, 30, 33]
new_labels: [0, 2, 3]
file: tfrecords\train_data_new\MX.tfrecord
new_labels: [11, 14]
new_labels: [4, 5]
new_labels: [4]
file: tfrecords\train_data_new\N0.tfrecord
new_labels: [2, 3]
file: tfrecords\train_data_new\n3.tfrecord
new_labels: [4, 5]
file: tfrecords\train_data_new\n4.tfrecord
new_labels: [0, 4]
file: tfrecords\train_data_new\n5.tfrecord
new_labels: [22, 23, 24

In [110]:
## Houd totale aantal bij
sum_occur = 0

## Laat # voorkomens per label zien
cnt_labels = Counter(all_labels)
for i in cnt_labels.most_common(len(all_labels)):
    sum_occur = sum_occur + i[1]
    print(mid_to_label_new.loc[np.int(i[0])]['display_name'], ' : ', str(i[1]))

Speech  :  769
Music  :  722
Gunshot, gunfire  :  349
Vehicle  :  250
Animal  :  226
Gunshot SC9mm  :  207
Musical instrument  :  185
Domestic animals, pets  :  160
Car  :  111
Gunshot SC556  :  77
Emergency vehicle  :  47
Rail transport  :  43
Aircraft  :  36
Idling  :  29
Boat, Water vehicle  :  29
Ambulance (siren)  :  28
Medium engine (mid frequency)  :  27
Car passing by  :  27
Motor vehicle (road)  :  26
Engine starting  :  25
Jackhammer  :  25
Machine gun  :  24
Motorcycle  :  23
Train wheels squealing  :  22
Heavy engine (low frequency)  :  21
Traffic noise, roadway noise  :  21
Fire engine, fire truck (siren)  :  21
Hammer  :  20
Accelerating, revving, vroom  :  19
Police car (siren)  :  19
Chainsaw  :  19
Tools  :  19
Bus  :  19
Conversation  :  18
Power tool  :  17
Vehicle horn, car horn, honking  :  15


In [111]:
#label_combinations = getLabelCombinations(balanced_train_segments)
#label_combinations = getLabelCombinations(unbalanced_train_segments)

## Bereken aantal voorkomens per combinatie
cnt_label_combinations = Counter(seq[i:j]
                   for seq in map(tuple, label_combinations)
                   for i, j in combinations(range(len(seq) + 1), 2))

In [23]:
## Haal labelnaam op en print aantal voorkomens (met top x)
for label_combination in cnt_label_combinations.most_common(1000):
    
    if(label_combination[1]<2): # vanaf 2x voorkomen
        break;
        
    label_names = []
    for i in label_combination[0]:
        label_names.append(str(mid_to_label_new.loc[np.int(i)]['display_name']))
    label_names = ', '.join(label_names)
    print(label_names,': ', label_combination[1])

Speech :  818
Conversation :  435
Conversation, Musical instrument :  346
Musical instrument :  346
Conversation, Musical instrument, Conversation :  283
Conversation, Musical instrument, Conversation, Musical instrument :  283
Musical instrument, Conversation :  283
Musical instrument, Conversation, Musical instrument :  283
Animal :  281
Conversation, Musical instrument, Conversation, Musical instrument, Conversation :  281
Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument :  281
Musical instrument, Conversation, Musical instrument, Conversation :  281
Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument :  281
Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation :  280
Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument :  280
Musical instrument, Conversati

Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation :  262
Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

...

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru

Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instrument, Conversation, Musical instru